```bash
%%shell
# Installs the latest dev build of TVM from PyPI. If you wish to build
# from source, see https://tvm.apache.org/docs/install/from_source.html
pip install apache-tvm --pre
```

# 元张量函数变换
在本节中，我们将介绍编译流程的主要组成部分——元张量函数变换。


In [1]:
%cd ..
import set_env

/media/pc/data/lxw/ai/tvm-book/doc/tutorials


In [2]:
import tvm
from tvm.script import ir as I
from tvm.script import tir as T


@I.ir_module
class MyModule:
    @T.prim_func
    def main(
        A: T.Buffer((128, 128), "float32"),
        B: T.Buffer((128, 128), "float32"),
        C: T.Buffer((128, 128), "float32"),
    ):
        T.func_attr({"tir.noalias": T.bool(True)})
        Y = T.alloc_buffer((128, 128))
        for i, j, k in T.grid(128, 128, 128):
            with T.block("Y"):
                vi, vj, vk = T.axis.remap("SSR", [i, j, k])
                with T.init():
                    Y[vi, vj] = T.float32(0)
                Y[vi, vj] = Y[vi, vj] + A[vi, vk] * B[vk, vj]
        for i, j in T.grid(128, 128):
            with T.block("C"):
                vi, vj = T.axis.remap("SS", [i, j])
                C[vi, vj] = T.max(Y[vi, vj], T.float32(0))

在我们转换函数之前，让我们先评估原始实现的性能。

In [3]:
import numpy as np

a_np = np.random.uniform(size=(128, 128)).astype("float32")
b_np = np.random.uniform(size=(128, 128)).astype("float32")
c_np = a_np @ b_np

a_nd = tvm.nd.array(a_np)
b_nd = tvm.nd.array(b_np)
c_nd = tvm.nd.array(np.zeros((128, 128), dtype="float32"))


def evaluate(mod: tvm.IRModule):
    lib = tvm.build(mod, target="llvm")
    # check correctness
    lib(a_nd, b_nd, c_nd)
    np.testing.assert_allclose(c_nd.numpy(), c_np, rtol=1e-5)
    # evaluate performance
    f_timer = lib.time_evaluator("main", tvm.cpu())
    print(f_timer(a_nd, b_nd, c_nd))


evaluate(MyModule)

Execution time summary:
 mean (ms)   median (ms)    max (ms)     min (ms)     std (ms)  
   3.3629       3.3629       3.3629       3.3629       0.0000                  


## 初始化调度
我们通过使用提供的**MyModule**作为输入来建立一个Schedule帮助类，以此启动代码转换的过程。

In [4]:
sch = tvm.tir.Schedule(MyModule)

## 循环平铺(Tiling)
接下来，我们执行必要的操作来获取块 **Y** 及其关联循环的引用。

In [5]:
block_Y = sch.get_block("Y")
i, j, k = sch.get_loops(block_Y)

我们现在开始执行转换。第一个修改是将循环``j``拆分为两个独立的循环，内层循环的长度为4。必须了解的是，转换过程是分步进行的；因此，如果无意中再次执行块，将会出现一个错误，指出变量``j``不存在。

In [6]:
j0, j1 = sch.split(j, factors=[None, 8])

转换的结果可以被检查，因为它被保留在``sch.mod``中。

In [7]:
sch.mod.show()

在初始转换阶段之后，生成了两个补充循环``j_0``和``j_1``，它们的范围分别为32和4。接下来的动作是重新排序这两个循环。

In [8]:
sch.reorder(j0, k, j1)
sch.mod.show()
evaluate(sch.mod)

Execution time summary:
 mean (ms)   median (ms)    max (ms)     min (ms)     std (ms)  
   1.1184       1.1184       1.1184       1.1184       0.0000                  


## 利用局部性
接下来，我们将执行两个额外的转换步骤以获得不同的变体。首先，我们使用一个名为**reverse_compute_at**的原语将块**C**移动到**Y**的内层循环中。

In [9]:
block_C = sch.get_block("C")
sch.reverse_compute_at(block_C, j0)
sch.mod.show()

## 重写约简
到目前为止，约简初始化和更新步骤一直保留在同一个块体中。这种混合形式便于循环转换，因为初始化和更新的外部循环``i``, ``j``通常需要保持同步。

在循环转换之后，我们可以使用**decompose_reduction**原语将Y元素的初始化与约简更新分开。

In [10]:
sch.decompose_reduction(block_Y, k)
sch.mod.show()
evaluate(sch.mod)

Execution time summary:
 mean (ms)   median (ms)    max (ms)     min (ms)     std (ms)  
   0.4299       0.4299       0.4299       0.4299       0.0000                  


## 跟踪转换
TensorIR调度是一种过程语言，转换是以逐步方式执行的。我们可以通过打印调度或调度的历史来跟踪转换。

我们已经通过打印``sch.mod``看到了调度。我们还可以通过``sch.trace``打印调度的历史。

In [11]:
sch.trace.show()

或者，我们可以结合历史跟踪输出IRModule。

In [12]:
sch.show()